In [91]:
# Step 1: Data Preprocessing
import pandas as pd
from tqdm import tqdm

# Read the xlsx file into a DataFrame
# Data from:
# https://nsidc.org/arcticseaicenews/sea-ice-tools/
# All daily (single day and five-day trailing average) extent values in one file, updated daily (Sea_Ice_Index_Daily_Extent_G02135_v3.0.xlsx)
file_path = 'Sea_Ice_Index_Daily_Extent_G02135_v3.0.xlsx'
df = pd.read_excel(file_path, engine='openpyxl', header=None)

# Extract the year values from the first column after removing non-numeric entries
years = df.iloc[0, 2:-3].dropna().astype(int).values

# Forward-fill missing month names with the previous non-NaN month value
df[0].fillna(method='ffill', inplace=True)

# make sure it has the right number of rows (1 + 366 = 367)
df = df.iloc[:367]

# Drop the first row (year header) and reset the index
df = df.iloc[1:].reset_index(drop=True)

# Drop the last three columns and reset the index
df = df.iloc[:, 0:-3].reset_index(drop=True)

# Preprocess the data for prophet package (ds and y columns)

# Initialize variables to hold month and day information
month = ''
day = ''

# Create a new DataFrame with the 'ds' and 'y' columns
df_new = pd.DataFrame(columns=['ds', 'y'])

df_new_row_index = 0

# Iterate through, column by column (skipping the first two)
for col_index in range(2, df.shape[1]):
    year = years[col_index - 2]
    print(f"Pre-processing data for year {year} ...")
    
    # Iterate through the DataFrame rows
    for index, row in df.iterrows():
        # If the row has a non-NaN value in the first column, it contains the month name
        if pd.notna(row[0]):
            month = row[0]
            day = int(row[1])
            
        # Check if the date falls on February 29 and if it is a non-leap year
        leap_year = (year % 4 == 0)
        if month == 'February' and day == 29 and not leap_year:
            # Skips this date since it is not a real date and there is no data
            continue

        # Construct the date string by combining month, day, and year information
        year_str = str(int(year))
        day_str = str(int(day))
        date_str = f"{month} {day_str}, {year_str}"

        # Add the constructed date strings as the 'ds' column in the DataFrame
        new_ds_value = pd.to_datetime(date_str, format='%B %d, %Y', errors='coerce')
        new_y_value = row[col_index]
        
        # Append the new 'ds' and 'y' values to the DataFrame
        df_new.loc[df_new_row_index, 'ds'] = new_ds_value
        df_new.loc[df_new_row_index, 'y'] = new_y_value
        df_new_row_index += 1
    
# Set any missing or empty values to NaN
df_new.replace(r'^\s*$', pd.NA, regex=True, inplace=True)

Pre-processing data for year 1978 ...
Pre-processing data for year 1979 ...
Pre-processing data for year 1980 ...
Pre-processing data for year 1981 ...
Pre-processing data for year 1982 ...
Pre-processing data for year 1983 ...
Pre-processing data for year 1984 ...
Pre-processing data for year 1985 ...
Pre-processing data for year 1986 ...
Pre-processing data for year 1987 ...
Pre-processing data for year 1988 ...
Pre-processing data for year 1989 ...
Pre-processing data for year 1990 ...
Pre-processing data for year 1991 ...
Pre-processing data for year 1992 ...
Pre-processing data for year 1993 ...
Pre-processing data for year 1994 ...
Pre-processing data for year 1995 ...
Pre-processing data for year 1996 ...
Pre-processing data for year 1997 ...
Pre-processing data for year 1998 ...
Pre-processing data for year 1999 ...
Pre-processing data for year 2000 ...
Pre-processing data for year 2001 ...
Pre-processing data for year 2002 ...
Pre-processing data for year 2003 ...
Pre-processi

In [92]:
# Remove empty values from future dates at end of the frame
# Find the index of the last non-empty 'y' value starting from the last row
last_non_empty_y_index = None
for i in range(len(df_new) - 1, -1, -1):
    if pd.notna(df_new.loc[i, 'y']):
        last_non_empty_y_index = i
        break

# If no non-empty 'y' value is found, the DataFrame will be empty
if last_non_empty_y_index is not None:
    # Slice the DataFrame to keep rows from last_non_empty_y_index onwards
    df_new = df_new.loc[0:last_non_empty_y_index]

print('Done pre-processing data:')
print(df_new)


Done pre-processing data:
              ds      y
0     1978-01-01    NaN
1     1978-01-02    NaN
2     1978-01-03    NaN
3     1978-01-04    NaN
4     1978-01-05    NaN
...          ...    ...
16634 2023-07-18  8.041
16635 2023-07-19  7.857
16636 2023-07-20  7.640
16637 2023-07-21  7.629
16638 2023-07-22  7.604

[16639 rows x 2 columns]


In [93]:
# optional linear interpolation (never used)
num_missing_values = df_new['y'].isna().sum()

print("Number of missing values in 'y' column:", num_missing_values)

df_interp = df_new.copy()

# Perform linear interpolation for missing values in the 'y' column
df_interp['y'] = df_interp['y'].interpolate(method='linear', axis=0, limit_area='inside', limit_direction='both')

num_missing_values = df_interp['y'].isna().sum()

print("Number of missing values in 'y' column:", num_missing_values)


Number of missing values in 'y' column: 1949
Number of missing values in 'y' column: 298


In [94]:
# Step 2: Install and Import Required Libraries
# You might need to install fbprophet using "pip install fbprophet" first.
from prophet import Prophet

def doForecast(df_historical, period):
    # Step 3: Forecasting with Prophet
    # Create a Prophet model
    model = Prophet(interval_width=0.995, seasonality_mode='additive', yearly_seasonality=True, weekly_seasonality=False, daily_seasonality=False)
    
    # Fit the model to your data
    model.fit(df_historical)

    # Create a DataFrame with future dates for prediction
    future_dates = model.make_future_dataframe(periods=period, include_history=False)  # Forecasting 365 days into the future

    # Make predictions for the future dates
    forecast = model.predict(future_dates)
    return forecast, model

def doForecastWithParams(df_historical, period, changepoint_prior_scale, seasonality_prior_scale, change_dates = None):
    # Step 3: Forecasting with Prophet
    # Create a Prophet model
    model = Prophet(interval_width=0.995, changepoints=change_dates, changepoint_prior_scale=changepoint_prior_scale, seasonality_prior_scale=seasonality_prior_scale, seasonality_mode='additive', yearly_seasonality=True, weekly_seasonality=False, daily_seasonality=False)
    
    # Fit the model to your data
    model.fit(df_historical)

    # Create a DataFrame with future dates for prediction
    future_dates = model.make_future_dataframe(periods=period, include_history=False)  # Forecasting 365 days into the future

    # Make predictions for the future dates
    forecast = model.predict(future_dates)
    return forecast, model

def doForecastCross(df_historical, periods, params, change_dates = None):
    # Step 3: Forecasting with Prophet
    # Create a Prophet model
    # Adjusted hyper-parameter changepoint_prior_scale:
    # initial tuning suggests 0.5, 10 but this only gets the minimum and increases the error farther out for the max
    model = Prophet(interval_width=0.995, changepoints=change_dates, seasonality_mode='additive', yearly_seasonality=True, weekly_seasonality=False, daily_seasonality=False, **params)
    
    # Fit the model to your data
    model.fit(df_historical)

    # Create a DataFrame with future dates for prediction
    future_dates = model.make_future_dataframe(periods=period, include_history=False)  # Forecasting 365 days into the future

    # Make predictions for the future dates
    forecast = model.predict(future_dates)
    return forecast, model

In [95]:
# Do forecast for current year, for graph
# Period of days into the future to forecast
# For this graph we will use a whole year into the future to forecast
# Need to adjust the period down as we get near the minimum (mid-September)
#   in order to make sure we only calculate the minimum for this year
period = 365

# Without any tuning
#[forecast, model] = doForecast(df_new, period)

# With tuning from cross-validation

cutoff_date_timestamp = df_new['ds'].iloc[-1]
min_max_dates = ['1979-09-22', '1980-09-05', '1981-09-11', '1982-09-14', '1983-09-09', '1984-09-16', '1985-09-10', '1986-09-07', '1987-09-03', '1988-09-11', '1989-09-23', '1990-09-22', '1991-09-17', '1992-09-07', '1993-09-14', '1994-09-06', '1995-09-05', '1996-09-10', '1997-09-04', '1998-09-18', '1999-09-13', '2000-09-11', '2001-09-20', '2002-09-19', '2003-09-18', '2004-09-18', '2005-09-21', '2006-09-15', '2007-09-15', '2008-09-18', '2009-09-13', '2010-09-20', '2011-09-09', '2012-09-16', '2013-09-14', '2014-09-17', '2015-09-09', '2016-09-07', '2017-09-14', '2018-09-22', '2019-09-19', '2020-09-13', '2021-09-15', '2022-09-16', '1979-03-02', '1980-03-05', '1981-03-15', '1982-02-27', '1983-03-15', '1984-03-18', '1985-03-18', '1986-03-11', '1987-02-21', '1988-03-10', '1989-03-07', '1990-03-13', '1991-02-25', '1992-03-12', '1993-03-14', '1994-02-21', '1995-04-01', '1996-02-21', '1997-03-21', '1998-02-25', '1999-03-31', '2000-03-03', '2001-03-05', '2002-03-10', '2003-03-21', '2004-03-10', '2005-03-10', '2006-03-12', '2007-03-11', '2008-02-27', '2009-03-03', '2010-04-01', '2011-03-08', '2012-03-18', '2013-03-15', '2014-03-21', '2015-02-22', '2016-03-22', '2017-03-06', '2018-03-15', '2019-03-12', '2020-03-04', '2021-03-12', '2022-02-21', '2023-03-06']
# Convert the list of date strings to pandas Timestamp objects
timestamps = pd.to_datetime(min_max_dates)
# Filter the timestamps to include only dates before the cutoff_date
cutoff_change_dates = timestamps[timestamps <= cutoff_date_timestamp]
# Sort the Timestamps in increasing order
cutoff_change_dates = cutoff_change_dates.sort_values()
# Convert the filtered timestamps back to date strings
cutoff_change_dates_strings = cutoff_change_dates.strftime('%Y-%m-%d').tolist()

# see cross validation xlsx
# for 7-21 to 8-21: keep trend tight, and no regularization penalty for seasonality
# validation with tuning from cross-validation
changepoint_prior_scale = 0.001
seasonality_prior_scale = 10
[forecast, model] = doForecastWithParams(df_new, period, changepoint_prior_scale, seasonality_prior_scale, cutoff_change_dates_strings)

# Print the forecasted values
print("Forecast DataFrame:")
print(forecast)

18:57:05 - cmdstanpy - INFO - Chain [1] start processing
18:57:09 - cmdstanpy - INFO - Chain [1] done processing


Forecast DataFrame:
            ds      trend  yhat_lower  yhat_upper  trend_lower  trend_upper  \
0   2023-07-23  10.394669    6.329613    8.586751    10.394669    10.394670   
1   2023-07-24  10.394665    6.291235    8.596507    10.394665    10.394668   
2   2023-07-25  10.394661    6.182469    8.452712    10.394657    10.394668   
3   2023-07-26  10.394658    6.139970    8.273432    10.394648    10.394668   
4   2023-07-27  10.394654    6.174801    8.221989    10.394639    10.394669   
..         ...        ...         ...         ...          ...          ...   
360 2024-07-17  10.393247    6.669060    9.152531    10.387535    10.399825   
361 2024-07-18  10.393243    6.582994    9.109977    10.387507    10.399847   
362 2024-07-19  10.393239    6.724918    8.881259    10.387478    10.399869   
363 2024-07-20  10.393235    6.517736    8.733282    10.387450    10.399892   
364 2024-07-21  10.393232    6.467599    8.687215    10.387421    10.399915   

     additive_terms  additive_t

In [100]:
# Current year forecast graph 
import pandas as pd
import plotly.graph_objects as go
from prophet.plot import plot_plotly, plot_components_plotly

#pip install ipywidgets

# Assuming you have the forecast data in a DataFrame called forecast_df
forecast_df = forecast.loc[-365:]
# The DataFrame should contain a 'ds' column with the dates and a 'yhat' column with the forecasted values.

# Convert the 'ds' column to pandas datetime objects (if not already)
forecast_df['ds'] = pd.to_datetime(forecast_df['ds'])

# Plot the forecast using plot_plotly
fig = plot_plotly(model, forecast_df)
# Set the default range for the x-axis (datetimestamp)
start_date = pd.to_datetime('2012-01-01')
end_date = pd.to_datetime('2024-12-31')
fig.update_xaxes(range=[start_date, end_date])
fig.update_layout(title_text="Arctic Sea Ice-Extent Forecast only using historical data)")
fig.update_yaxes(title_text="Extent (10^6 km^2)")
fig.show()

# Plot the forecast components using plot_components_plotly
fig_comp = plot_components_plotly(model, forecast_df)
fig_comp.show()

In [99]:
# Calculate the current year forecast minimum values

forecasted_values = forecast['yhat']
forecasted_lower_bounds = forecast['yhat_lower']
forecasted_upper_bounds = forecast['yhat_upper']

# Print the minimum value for the forecast
min_forecast = forecasted_values.min()
print("Minimum Forecast Value:", round(min_forecast, 3))

# Print the ± range values for the forecast
print("Lower Bound:", round(forecasted_lower_bounds.min(),3))
print("Upper Bound:", round(forecasted_upper_bounds.min(),3))


Minimum Forecast Value: 4.841
Lower Bound: 3.565
Upper Bound: 5.805


In [98]:
# Repeat runs and check if any bounds contain threshold
threshold = 3.41
# run count
numruns = 20
# limit number of days for speed?
period = 120

threshold_in_range_count = 0
print(f"Check to see if threshold record for minimum ({threshold}) is in range of 99.5% interval for forecast for {numruns} runs")
for i in range(numruns):
    [forecast_run, model_run] = doForecast(df_new, period)
    forecasted_lower_bounds = forecast_run['yhat_lower'].min()
    forecasted_upper_bounds = forecast_run['yhat_upper'].min()
    min_forecast = orecasted_values = forecast_run['yhat'].min()
    threshold_in_range = (forecasted_lower_bounds <= threshold) and (threshold <= forecasted_upper_bounds)
    print(f"Run {i+1}")
    if threshold_in_range:
        print("Threshold in range!")
        threshold_in_range_count += 1
        print(" Minimum Forecast Value:", round(min_forecast, 3))
        # Print the ± range values for the forecast
        print("  99.5% Interval:")
        print("    Lower Bound:", round(forecasted_lower_bounds,3))
        print("    Upper Bound:", round(forecasted_upper_bounds,3))

pct_threshold_in_range = round(100 * threshold_in_range_count / numruns , 3)
print(f"Forecast has record minimum in range for {pct_threshold_in_range} % of the runs ({threshold_in_range_count} / {numruns})")


Check to see if threshold record for minimum (3.41) is in range of 99.5% interval for forecast for 20 runs


18:57:12 - cmdstanpy - INFO - Chain [1] start processing
18:57:25 - cmdstanpy - INFO - Chain [1] done processing


Run 1


18:57:27 - cmdstanpy - INFO - Chain [1] start processing
18:57:40 - cmdstanpy - INFO - Chain [1] done processing


Run 2


...

Run 18


19:01:37 - cmdstanpy - INFO - Chain [1] start processing
19:01:49 - cmdstanpy - INFO - Chain [1] done processing


Run 19


19:01:51 - cmdstanpy - INFO - Chain [1] start processing
19:02:03 - cmdstanpy - INFO - Chain [1] done processing


Run 20
Forecast has record minimum in range for 0.0 % of the runs (0 / 20)


In [ ]:
### VALIDATION AND CROSS VALIDATION BELOW

In [85]:
#### VALIDATION
import pandas as pd

# Number of iterations you want to perform (validate_years)
validate_years = 20
# Period of days into the future to forecast
# don't forecast too far into the future to make sure we only get the minimum for the year of interest
period = 180

df_truncated = df_new
# Loop to truncate data by one year for each iteration
total_abs_error = 0
forecast_in_range_count = 0

last_date = df_truncated['ds'].iloc[-1]
print(f"Validating forecast minimum value for {validate_years} years prior to last observation of: {last_date}")

for i in range(validate_years):

    # First get the previous year's minimum
    most_recent_year = df_truncated['ds'].dt.year.iloc[-1] - 1
    
    # Step 3: Use boolean indexing to slice the DataFrame for the identified year range
    start_date = pd.to_datetime(f'{most_recent_year}-01-01')
    end_date = pd.to_datetime(f'{most_recent_year}-12-31')
    df_most_recent_year = df_truncated[(df_truncated['ds'] >= start_date) & (df_truncated['ds'] <= end_date)]
    min_value = df_most_recent_year['y'].min()
    print(f"{most_recent_year}: {min_value}")
    
    # Get the last date in the current DataFrame
    last_date = df_truncated['ds'].iloc[-1]

    # Truncate data to one year prior
    one_year_prior = last_date - pd.DateOffset(years=1)

    # Slice the DataFrame to include data up to one year prior
    df_truncated = df_truncated[df_truncated['ds'] <= one_year_prior]
    
    cutoff_date_timestamp = df_truncated['ds'].iloc[-1]
    min_max_dates = ['1979-09-22', '1980-09-05', '1981-09-11', '1982-09-14', '1983-09-09', '1984-09-16', '1985-09-10', '1986-09-07', '1987-09-03', '1988-09-11', '1989-09-23', '1990-09-22', '1991-09-17', '1992-09-07', '1993-09-14', '1994-09-06', '1995-09-05', '1996-09-10', '1997-09-04', '1998-09-18', '1999-09-13', '2000-09-11', '2001-09-20', '2002-09-19', '2003-09-18', '2004-09-18', '2005-09-21', '2006-09-15', '2007-09-15', '2008-09-18', '2009-09-13', '2010-09-20', '2011-09-09', '2012-09-16', '2013-09-14', '2014-09-17', '2015-09-09', '2016-09-07', '2017-09-14', '2018-09-22', '2019-09-19', '2020-09-13', '2021-09-15', '2022-09-16', '1979-03-02', '1980-03-05', '1981-03-15', '1982-02-27', '1983-03-15', '1984-03-18', '1985-03-18', '1986-03-11', '1987-02-21', '1988-03-10', '1989-03-07', '1990-03-13', '1991-02-25', '1992-03-12', '1993-03-14', '1994-02-21', '1995-04-01', '1996-02-21', '1997-03-21', '1998-02-25', '1999-03-31', '2000-03-03', '2001-03-05', '2002-03-10', '2003-03-21', '2004-03-10', '2005-03-10', '2006-03-12', '2007-03-11', '2008-02-27', '2009-03-03', '2010-04-01', '2011-03-08', '2012-03-18', '2013-03-15', '2014-03-21', '2015-02-22', '2016-03-22', '2017-03-06', '2018-03-15', '2019-03-12', '2020-03-04', '2021-03-12', '2022-02-21', '2023-03-06']

    # Convert the list of date strings to pandas Timestamp objects
    timestamps = pd.to_datetime(min_max_dates)

    # Filter the timestamps to include only dates before the cutoff_date
    cutoff_change_dates = timestamps[timestamps <= cutoff_date_timestamp]

    # Sort the Timestamps in increasing order
    cutoff_change_dates = cutoff_change_dates.sort_values()

    # Convert the filtered timestamps back to date strings
    cutoff_change_dates_strings = cutoff_change_dates.strftime('%Y-%m-%d').tolist()

    # see cross validation xlsx
    # for 7-21 to 8-21: keep trend tight, and no regularization penalty for seasonality
    # validation with tuning from cross-validation
    changepoint_prior_scale = 0.001
    seasonality_prior_scale = 10
    [validate_forecast, model] = doForecastWithParams(df_truncated, period, changepoint_prior_scale, seasonality_prior_scale, cutoff_change_dates_strings)
    # validation without any tuning:
    # [validate_forecast, model] = doForecastWithParams(df_truncated, period)
    
    forecasted_values = validate_forecast['yhat']
    forecasted_lower_bounds = validate_forecast['yhat_lower']
    forecasted_upper_bounds = validate_forecast['yhat_upper']

    # Print the minimum value for the forecast
    min_value_forecast = forecasted_values.min()
    min_value_error = min_value - min_value_forecast
    total_abs_error += abs(min_value_error)
    print(f"{most_recent_year}")
    print("  Minimum Forecast Value: " + str(round(min_value_forecast, 3)))
    print("  Actual Minimum Value: " + str(round(min_value, 3)))
    print("  Error: " + str(round(min_value_error, 3)))
    print("")
    # Print the ± range values for the forecast
    forecast_lower = forecasted_lower_bounds.min()
    forecast_upper = forecasted_upper_bounds.min()
    forecast_in_range = (forecast_lower <= min_value) and (min_value <= forecast_upper)
    if forecast_in_range:
        forecast_in_range_count += 1
        is_in_range = "YES"
    else:
        is_in_range = "NO"
    print("  Forecast 99.5% Interval:")
    print("    Lower Bound: " + str(round(forecast_lower,3)))
    print("    Upper Bound: " + str(round(forecast_upper,3)))
    print("")
    print(f"  Forecast in 99.5% Interval?: {is_in_range}")
    print("")

avg_abs_error = round(total_abs_error / validate_years, 3)
in_range_pct = round(100 * (forecast_in_range_count / validate_years), 3)
print("")
print("Validation Summary:")
print(f"  Average (absolute) Error: {avg_abs_error}")
print(f"  Predictions that actual min value was in forecasted 99.5% Range: {in_range_pct} % ({forecast_in_range_count} out of {validate_years})" )


Validating forecast minimum value for 20 years prior to last observation of: 2023-07-21 00:00:00
2022: 4.692


18:39:19 - cmdstanpy - INFO - Chain [1] start processing
18:39:24 - cmdstanpy - INFO - Chain [1] done processing


2022
  Minimum Forecast Value: 4.717
  Actual Minimum Value: 4.692
  Error: -0.025

  Forecast 99.5% Interval:
    Lower Bound: 3.468
    Upper Bound: 5.766

  Forecast in 99.5% Interval?: YES

2021: 4.757


18:39:25 - cmdstanpy - INFO - Chain [1] start processing
18:39:27 - cmdstanpy - INFO - Chain [1] done processing


2021
  Minimum Forecast Value: 4.618
  Actual Minimum Value: 4.757
  Error: 0.139

  Forecast 99.5% Interval:
    Lower Bound: 3.358
    Upper Bound: 5.606

  Forecast in 99.5% Interval?: YES

2020: 3.793


...

2005
  Minimum Forecast Value: 5.902
  Actual Minimum Value: 5.314
  Error: -0.588

  Forecast 99.5% Interval:
    Lower Bound: 4.968
    Upper Bound: 6.68

  Forecast in 99.5% Interval?: YES

2004: 5.77


18:40:22 - cmdstanpy - INFO - Chain [1] start processing
18:40:24 - cmdstanpy - INFO - Chain [1] done processing


2004
  Minimum Forecast Value: 6.078
  Actual Minimum Value: 5.77
  Error: -0.308

  Forecast 99.5% Interval:
    Lower Bound: 5.16
    Upper Bound: 6.88

  Forecast in 99.5% Interval?: YES

2003: 5.969


18:40:25 - cmdstanpy - INFO - Chain [1] start processing
18:40:26 - cmdstanpy - INFO - Chain [1] done processing


2003
  Minimum Forecast Value: 6.208
  Actual Minimum Value: 5.969
  Error: -0.239

  Forecast 99.5% Interval:
    Lower Bound: 5.274
    Upper Bound: 7.024

  Forecast in 99.5% Interval?: YES


Validation Summary:
  Average (absolute) Error: 0.536
  Predictions that actual min value was in forecasted 99.5% Range: 90.0 % (18 out of 20)


In [69]:
## CROSS VALIDATION for different start days (so there are less days until the minimum)
import pandas as pd
import itertools

# Number of iterations you want to perform (validate_years)
validate_years = 20

# Period of days into the future to forecast
# don't forecast too far into the future to make sure we only get the minimum for the year of interest
period = 180

# years to validate (use from previous run) (for testing only)
#years_to_validate = [2012, 2011, 2006]
#years_to_validate = [2012]
years_to_validate = list(range(2023-validate_years, 2023))

param_grid = {  
    'changepoint_prior_scale': [0.001, 0.01, 0.1, 0.5],
    'seasonality_prior_scale': [0.01, 0.1, 1.0, 10.0],
}

"""
param_grid = {  
    'changepoint_prior_scale': [0.001, 0.5],
    'seasonality_prior_scale': [0.01, 10.0],
}
"""


# Generate all combinations of parameters
all_params = [dict(zip(param_grid.keys(), v)) for v in itertools.product(*param_grid.values())]
maes = []
rmses = []  # Store the RMSEs for each params here
pct_in_interval = []

# Use cross validation to evaluate all parameters
for params in all_params:
    
    for k in [49, 42, 35, 28, 14, 7]:
    #for k in [49]:
        print(f"For +{k} days from last observation:")
        df_truncated = df_new # Loop to truncate data by one year for each iteration
        total_abs_error = 0
        total_sq_error = 0
        
        forecast_in_range_count = 0

        future_date = df_truncated['ds'].iloc[-1] + pd.DateOffset(days=k)
        print(f"Validating forecast for {validate_years} prior to most recent year's observation, for reference in future forecasts: {future_date}")
        
        
        for i in range(validate_years):
            # First get the previous year's minimum
            most_recent_year = df_truncated['ds'].dt.year.iloc[-1] - 1

            # Step 3: Use boolean indexing to slice the DataFrame for the identified year range
            start_date = pd.to_datetime(f'{most_recent_year}-01-01')
            end_date = pd.to_datetime(f'{most_recent_year}-12-31')
            df_most_recent_year = df_truncated[(df_truncated['ds'] >= start_date) & (df_truncated['ds'] <= end_date)]
            min_value = df_most_recent_year['y'].min()
            print(f"{most_recent_year}: {min_value}")

            # Get the last date in the current DataFrame
            last_date = df_truncated['ds'].iloc[-1]

            # Truncate data to one year prior (+ days for first period to get the correct offset)
            if i == 0:
                one_year_prior = last_date - pd.DateOffset(years=1) + pd.DateOffset(days=k)
            else:
                one_year_prior = last_date - pd.DateOffset(years=1)

            print(f"  Validating forecast minimum value forward from {one_year_prior}:")

            # Slice the DataFrame to include data up to one year prior
            df_truncated = df_truncated[df_truncated['ds'] <= one_year_prior]

            if int(one_year_prior.year) in years_to_validate:
                cutoff_date_timestamp = df_truncated['ds'].iloc[-1]
                min_max_dates = ['1979-09-22', '1980-09-05', '1981-09-11', '1982-09-14', '1983-09-09', '1984-09-16', '1985-09-10', '1986-09-07', '1987-09-03', '1988-09-11', '1989-09-23', '1990-09-22', '1991-09-17', '1992-09-07', '1993-09-14', '1994-09-06', '1995-09-05', '1996-09-10', '1997-09-04', '1998-09-18', '1999-09-13', '2000-09-11', '2001-09-20', '2002-09-19', '2003-09-18', '2004-09-18', '2005-09-21', '2006-09-15', '2007-09-15', '2008-09-18', '2009-09-13', '2010-09-20', '2011-09-09', '2012-09-16', '2013-09-14', '2014-09-17', '2015-09-09', '2016-09-07', '2017-09-14', '2018-09-22', '2019-09-19', '2020-09-13', '2021-09-15', '2022-09-16', '1979-03-02', '1980-03-05', '1981-03-15', '1982-02-27', '1983-03-15', '1984-03-18', '1985-03-18', '1986-03-11', '1987-02-21', '1988-03-10', '1989-03-07', '1990-03-13', '1991-02-25', '1992-03-12', '1993-03-14', '1994-02-21', '1995-04-01', '1996-02-21', '1997-03-21', '1998-02-25', '1999-03-31', '2000-03-03', '2001-03-05', '2002-03-10', '2003-03-21', '2004-03-10', '2005-03-10', '2006-03-12', '2007-03-11', '2008-02-27', '2009-03-03', '2010-04-01', '2011-03-08', '2012-03-18', '2013-03-15', '2014-03-21', '2015-02-22', '2016-03-22', '2017-03-06', '2018-03-15', '2019-03-12', '2020-03-04', '2021-03-12', '2022-02-21', '2023-03-06']

                # Convert the list of date strings to pandas Timestamp objects
                timestamps = pd.to_datetime(min_max_dates)

                # Filter the timestamps to include only dates before the cutoff_date
                cutoff_change_dates = timestamps[timestamps <= cutoff_date_timestamp]

                # Sort the Timestamps in increasing order
                cutoff_change_dates = cutoff_change_dates.sort_values()

                # Convert the filtered timestamps back to date strings
                cutoff_change_dates_strings = cutoff_change_dates.strftime('%Y-%m-%d').tolist()

                print("  Truncated data:")
                print(df_truncated)
                [validate_forecast, model] = doForecastCross(df_truncated, period, params, cutoff_change_dates_strings)

                forecasted_values = validate_forecast['yhat']
                forecasted_lower_bounds = validate_forecast['yhat_lower']
                forecasted_upper_bounds = validate_forecast['yhat_upper']

                # Print the minimum value for the forecast
                min_value_forecast = forecasted_values.min()
                min_value_error = min_value - min_value_forecast
                total_abs_error += abs(min_value_error)
                total_sq_error += (min_value_error ** 2)
                print(f"{most_recent_year}")
                print("  Forecasted values:")
                print(forecasted_values)
                print("")
                print("  Minimum Forecast Value: " + str(round(min_value_forecast, 3)))
                print("  Actual Minimum Value: " + str(round(min_value, 3)))
                print("  Error: " + str(round(min_value_error, 3)))
                print("")
                # Print the ± range values for the forecast
                forecast_lower = forecasted_lower_bounds.min()
                forecast_upper = forecasted_upper_bounds.min()
                forecast_in_range = (forecast_lower <= min_value) and (min_value <= forecast_upper)
                if forecast_in_range:
                    forecast_in_range_count += 1
                    is_in_range = "YES"
                else:
                    is_in_range = "NO"
                print("  Forecast 99.5% Interval:")
                print("    Lower Bound: " + str(round(forecast_lower,3)))
                print("    Upper Bound: " + str(round(forecast_upper,3)))
                print("")
                print(f"  Forecast in 99.5% Interval?: {is_in_range}")
                print("")
                
            else:
                print("  Skipping year for validation")
                print("")

        avg_abs_error = total_abs_error / validate_years
        maes.append(avg_abs_error)
        avg_abs_error = round(avg_abs_error, 3)
        rmses.append((total_sq_error ** 0.5) / validate_years)
        
        in_range_pct = round(100 * (forecast_in_range_count / validate_years), 3)
        pct_in_interval.append(in_range_pct)
        print("")
        print(f"Validation Summary for reference in {future_date}:")
        print(f"  Average (absolute) Error: {avg_abs_error}")
        print(f"  Predictions that actual min value was in forecasted 99.5% Range: {in_range_pct} % ({forecast_in_range_count} out of {validate_years})" )
        print("")
        print("")
        print("")

For +49 days from last observation:
Validating forecast for 20 prior to most recent year's observation, for reference in future forecasts: 2023-09-08 00:00:00
2022: 4.692
  Validating forecast minimum value forward from 2022-09-08 00:00:00:
  Truncated data:
              ds      y
0     1978-01-01    NaN
1     1978-01-02    NaN
2     1978-01-03    NaN
3     1978-01-04    NaN
4     1978-01-05    NaN
...          ...    ...
16317 2022-09-04  4.908
16318 2022-09-05  4.900
16319 2022-09-06  4.866
16320 2022-09-07  4.886
16321 2022-09-08  4.916

[16322 rows x 2 columns]


23:59:03 - cmdstanpy - INFO - Chain [1] start processing
23:59:07 - cmdstanpy - INFO - Chain [1] done processing


2022
  Forecasted values:
0       5.336330
1       5.328041
2       5.322518
3       5.319859
4       5.320161
         ...    
175    13.991492
176    13.995207
177    13.997802
178    13.999286
179    13.999675
Name: yhat, Length: 180, dtype: float64

  Minimum Forecast Value: 5.32
  Actual Minimum Value: 4.692
  Error: -0.628

  Forecast 99.5% Interval:
    Lower Bound: 3.8
    Upper Bound: 6.663

  Forecast in 99.5% Interval?: YES

2021: 4.757
  Validating forecast minimum value forward from 2021-09-08 00:00:00:
  Truncated data:
              ds      y
0     1978-01-01    NaN
1     1978-01-02    NaN
2     1978-01-03    NaN
3     1978-01-04    NaN
4     1978-01-05    NaN
...          ...    ...
15952 2021-09-04  5.073
15953 2021-09-05  4.973
15954 2021-09-06  4.897
15955 2021-09-07  4.895
15956 2021-09-08  4.893

[15957 rows x 2 columns]


23:59:08 - cmdstanpy - INFO - Chain [1] start processing
23:59:14 - cmdstanpy - INFO - Chain [1] done processing


2021
  Forecasted values:
0       5.308311
1       5.300844
2       5.296137
3       5.294289
4       5.295400
         ...    
175    13.869405
176    13.873039
177    13.875556
178    13.876962
179    13.877272
Name: yhat, Length: 180, dtype: float64

  Minimum Forecast Value: 5.294
  Actual Minimum Value: 4.757
  Error: -0.537

  Forecast 99.5% Interval:
    Lower Bound: 3.811
    Upper Bound: 6.645

  Forecast in 99.5% Interval?: YES

2020: 3.793
  Validating forecast minimum value forward from 2020-09-08 00:00:00:
  Truncated data:
              ds      y
0     1978-01-01    NaN
1     1978-01-02    NaN
2     1978-01-03    NaN
3     1978-01-04    NaN
4     1978-01-05    NaN
...          ...    ...
15587 2020-09-04  3.908
15588 2020-09-05  3.898
15589 2020-09-06  3.899
15590 2020-09-07  3.878
15591 2020-09-08  3.845

[15592 rows x 2 columns]


...

2005
  Forecasted values:
0       8.042276
1       7.968960
2       7.896900
3       7.826148
4       7.756753
         ...    
175    13.623020
176    13.656555
177    13.689107
178    13.720661
179    13.751214
Name: yhat, Length: 180, dtype: float64

  Minimum Forecast Value: 6.144
  Actual Minimum Value: 5.314
  Error: -0.83

  Forecast 99.5% Interval:
    Lower Bound: 5.33
    Upper Bound: 6.732

  Forecast in 99.5% Interval?: NO

2004: 5.77
  Validating forecast minimum value forward from 2004-07-28 00:00:00:
  Truncated data:
             ds      y
0    1978-01-01    NaN
1    1978-01-02    NaN
2    1978-01-03    NaN
3    1978-01-04    NaN
4    1978-01-05    NaN
...         ...    ...
9701 2004-07-24  8.820
9702 2004-07-25  8.760
9703 2004-07-26  8.653
9704 2004-07-27  8.466
9705 2004-07-28  8.431

[9706 rows x 2 columns]


17:33:06 - cmdstanpy - INFO - Chain [1] start processing
17:33:32 - cmdstanpy - INFO - Chain [1] done processing


2004
  Forecasted values:
0       8.202840
1       8.127645
2       8.053834
3       7.981473
4       7.910618
         ...    
175    13.910728
176    13.944523
177    13.977352
178    14.009210
179    14.040099
Name: yhat, Length: 180, dtype: float64

  Minimum Forecast Value: 6.298
  Actual Minimum Value: 5.77
  Error: -0.528

  Forecast 99.5% Interval:
    Lower Bound: 5.554
    Upper Bound: 6.907

  Forecast in 99.5% Interval?: YES

2003: 5.969
  Validating forecast minimum value forward from 2003-07-28 00:00:00:
  Truncated data:
             ds      y
0    1978-01-01    NaN
1    1978-01-02    NaN
2    1978-01-03    NaN
3    1978-01-04    NaN
4    1978-01-05    NaN
...         ...    ...
9335 2003-07-24  8.408
9336 2003-07-25  8.298
9337 2003-07-26  8.305
9338 2003-07-27  8.294
9339 2003-07-28  8.234

[9340 rows x 2 columns]


17:33:33 - cmdstanpy - INFO - Chain [1] start processing
17:33:56 - cmdstanpy - INFO - Chain [1] done processing


2003
  Forecasted values:
0       8.175186
1       8.097740
2       8.021650
3       7.946969
4       7.873746
         ...    
175    12.752101
176    12.778724
177    12.804419
178    12.829164
179    12.852945
Name: yhat, Length: 180, dtype: float64

  Minimum Forecast Value: 6.126
  Actual Minimum Value: 5.969
  Error: -0.157

  Forecast 99.5% Interval:
    Lower Bound: 5.416
    Upper Bound: 6.706

  Forecast in 99.5% Interval?: YES


Validation Summary for reference in 2023-07-28 00:00:00:
  Average (absolute) Error: 0.906
  Predictions that actual min value was in forecasted 99.5% Range: 65.0 % (13 out of 20)





In [ ]:
# Find the best parameters
#tuning_results = pd.DataFrame(all_params)
forecast_from_date = ['09-08', '09-01', '08-25', '08-18', '08-04', '07-28']
param_grid_with_dates = param_grid.copy()
param_grid_with_dates['date'] = forecast_from_date
all_params_with_dates = [dict(zip(param_grid_with_dates.keys(), v)) for v in itertools.product(*param_grid_with_dates.values())]
tuning_results = pd.DataFrame(all_params_with_dates)
tuning_results['rmses'] = rmses
tuning_results['maes'] = maes
tuning_results['pct_in_interval'] = pct_in_interval

In [77]:
with pd.option_context('display.max_rows', None,
                       'display.max_columns', None,
                       'display.precision', 3,
                       'display.width', 100,
                       ):
    print(tuning_results)

    changepoint_prior_scale  seasonality_prior_scale   date  rmses   maes  pct_in_interval
0                     0.001                     0.01  09-08  0.258  1.038             75.0
1                     0.001                     0.01  09-01  0.260  1.047             75.0
2                     0.001                     0.01  08-25  0.261  1.051             75.0
3                     0.001                     0.01  08-18  0.261  1.051             75.0
4                     0.001                     0.01  08-04  0.261  1.051             65.0
5                     0.001                     0.01  07-28  0.262  1.053             70.0
6                     0.001                     0.10  09-08  0.255  1.022             80.0
7                     0.001                     0.10  09-01  0.258  1.032             80.0
8                     0.001                     0.10  08-25  0.258  1.036             75.0
9                     0.001                     0.10  08-18  0.258  1.034             80.0